In [1]:
import os
from time import time
import numpy as np
import pandas as pd
import netCDF4 as nc
import matplotlib.pyplot as plt
import cartopy.crs as ccrs
from cartopy.feature import GSHHSFeature
from cartopy.mpl.ticker import LongitudeFormatter, LatitudeFormatter
import xarray as xr
from scipy import interpolate
from datetime import date
import math
from scipy import signal

C:\Users\oa18724\Anaconda3\envs\dl_env\lib\site-packages\scipy\__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.23.1
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


In [2]:
omega = 7.2921e-5

In [3]:
def plot_drifter_trajectories(df, direction=None, global_extent=False):
    ids = df['id'].unique()
    for id in ids:
        # df_id = df_id[1:-1]
        df_id = df.loc[df['id']==id]
        fig = plt.figure(figsize=(20,12))
        crs = ccrs.PlateCarree()
        ax = fig.add_subplot(1, 1, 1, projection=crs)
        ax.add_feature(GSHHSFeature(scale='intermediate', facecolor='lightgrey', linewidth=0.2))
        ax.set_xticks(np.linspace(-180, 180, 19), crs=crs)
        ax.set_yticks(np.linspace(-90, 90, 19), crs=crs)
        lon_formatter = LongitudeFormatter(zero_direction_label=True)
        lat_formatter = LatitudeFormatter()
        ax.xaxis.set_major_formatter(lon_formatter)
        ax.yaxis.set_major_formatter(lat_formatter)
        if global_extent:
            ax.set_global()
        # ax.gridlines()
        if direction=='v':
            plt.scatter(x=df_id.lon, y=df_id.lat, s=5, c=df_id.vn, transform=crs, cmap='jet')
        elif direction=='u':
            plt.scatter(x=df_id.lon, y=df_id.lat, s=5, c=df_id.ve, transform=crs, cmap='jet')
        elif direction=='corr_filt_v':
            plt.scatter(x=df_id.filt_lon, y=df_id.filt_lat, s=5, c=df_id.corr_vn, transform=crs, cmap='jet')
        elif direction=='corr_filt_u':
            plt.scatter(x=df_id.filt_lon, y=df_id.filt_lat, s=5, c=df_id.corr_ve, transform=crs, cmap='jet')
        else:
            plt.scatter(x=df_id.lon, y=df_id.lat, s=5, c=df_id.spd, transform=crs, cmap='jet')
            print('Displayed speed: input v for northward velocity or u for eastward')
        plt.show()

In [4]:
def plot_time_step(time_step_list, direction=None):
    fig = plt.figure(figsize=(20,12))
    crs = ccrs.PlateCarree()
    ax = fig.add_subplot(1, 1, 1, projection=crs)
    ax.add_feature(GSHHSFeature(scale='intermediate', facecolor='lightgrey', linewidth=0.2))
    ax.set_xticks(np.linspace(-180, 180, 19), crs=crs)
    ax.set_yticks(np.linspace(-90, 90, 19), crs=crs)
    lon_formatter = LongitudeFormatter(zero_direction_label=True)
    lat_formatter = LatitudeFormatter()
    ax.xaxis.set_major_formatter(lon_formatter)
    ax.yaxis.set_major_formatter(lat_formatter)
    ax.set_global()
    if direction=='v':
        plt.scatter(x=time_step_list.lon, y=time_step_list.lat, s=5, c=time_step_list.vn, transform=crs, cmap='jet')
    elif direction=='u':
        plt.scatter(x=time_step_list.lon, y=time_step_list.lat, s=5, c=time_step_list.ve, transform=crs, cmap='jet')
    else:
        plt.scatter(x=time_step_list.lon, y=time_step_list.lat, s=5, c=time_step_list.spd, transform=crs, cmap='jet')
        print('Displayed speed: input v for northward velocity or u for eastward')
    plt.show()

In [5]:
def get_time_step(df, years, months, days):
    df = df.copy()
    df_list = []
    # could replace nested for loop with hrs
    for year in years:
        for month in months:
            for day in days:
                # df = df.loc[df["spd"]<999.999]
                df_t = df.loc[(df['yy']==year) & (df['mm']==month) & (df['dd']==day)]
                df_list.append(df_t)
    return df_list

In [6]:
def get_time_step_over_month(df, years, months):
    df = df.copy()
    df_list = []
    for year in years:
        for month in months:
            # df = df.loc[df["spd"]<999.999]
            df_t = df.loc[(df['yy']==year) & (df['mm']==month)]
            df_list.append(df_t)
    return df_list

In [7]:
def get_drifter_vel(df, direction=None):
    df = df.copy()
    # df = df.loc[df["spd"]<999.999]
    if direction == 'v':
        return df['vn']
    elif direction == 'u':
        return df['ve']
    else:
        return df['spd']


In [8]:
def add_hours_column(df):
    df = df.copy()
    days, mnths, yrs = df['dd'], df['mm'], df['yy']
    conv_times = []
    for yr, mnth, day in zip(yrs, mnths, days):
        t = convert_time_to_hrs(year=yr, month=mnth, day=day)
        conv_times.append(t)
    df['hrs'] = conv_times
    return df

In [9]:
def convert_time_to_hrs(year, month, day):
    d_split = math.modf(day)
    d0 = date(1900, 1, 1)
    d1 = date(year, month, int(d_split[1]))
    diff = (d1 - d0)
    hours = (diff.days + d_split[0]) * 24
    return hours

In [10]:
def read_dat_file(path, filename):
    filepath = os.path.join(os.path.normpath(path), filename)
    fid = open(filepath, mode='r')
    df = pd.read_csv(fid, sep="\s+", header=None)
    return df

In [11]:
def read_drifters_to_df(path, filename, headers):
    df = read_dat_file(path, filename)
    df.columns = headers
    df.astype(float)
    df = df.loc[df["spd"]<999.999]
    return df

In [12]:
def correct_velocities_wind_slip(df):
    df = df.copy()
    df['corr_ve'] = 0
    df['corr_vn'] = 0
    df['wind_u10'] = 0
    df['wind_v10'] = 0
    yrs = sorted(df['yy'].unique())
    print(yrs)
    for yr in yrs:
        print(yr)
        fpath = f'D:/era5/download_{yr}.nc'
        if os.path.exists(fpath):
            print(fpath)
            wind_dataset = nc.Dataset(fpath)
            df = subtract_windslip(df, wind_dataset)
        else:
            print(f'{yr} era5 file does not exist')
    return df

In [13]:
def subtract_windslip(df, wind_dataset):
    df = df.copy()
    times = wind_dataset.variables['time'][:]
    u10, v10 = wind_dataset.variables['u10'], wind_dataset.variables['v10']
    lats, lons = wind_dataset.variables['latitude'][:], wind_dataset.variables['longitude'][:]
    for i, time in enumerate(times):
        f_u10 = interpolate.interp2d(lons, lats, u10[i], kind='cubic')
        f_v10 = interpolate.interp2d(lons, lats, v10[i], kind='cubic')
        df_t = df.loc[df["hrs"]==time]
        indices = df.index[df["hrs"]==time]
        # any_true = np.any(df["hrs"]==time)
        # if any_true:
            # print(i, f"there was a match!!!")
        u10_new = df_t.apply(lambda x: f_u10(x['lon'], x['lat'])[0], axis=1)
        v10_new = df_t.apply(lambda x: f_v10(x['lon'], x['lat'])[0], axis=1)
        wind_slip_u = u10_new * 0.07
        wind_slip_v = v10_new * 0.07
        df.loc[indices,'corr_ve'] = df_t['ve'] - wind_slip_u
        df.loc[indices,'corr_vn'] = df_t['vn'] - wind_slip_v
        df.loc[indices, 'wind_u10'] = u10_new
        df.loc[indices, 'wind_v10'] = v10_new
    return df

In [14]:
def filter_inertial_motion(df):
    df = df.copy()
    ids = df['id'].unique()

    for id in ids:
        df_id = df.loc[df['id']==id]
        indices = df.index[df["id"]==id]

        corr_vn = np.array(df_id['corr_vn'])
        corr_ve = np.array(df_id['corr_ve'])
        lons = np.array(df_id['lon'])
        lats = np.array(df_id['lat'])
        lats[lats == 0] = 0.01
        n = len(lats)
        f = 2*omega*np.sin(lats)
        T = (2*np.pi/(f))/3600
        w = (np.floor(np.abs(T/6))).astype(int)

        filt_lats = np.zeros(n)
        filt_lons = np.zeros(n)
        filt_ve = np.zeros(n)
        filt_vn = np.zeros(n)
        for i in range(n):
            left_w = min(w[i], i)
            right_w = min(w[i], n-i-1)
            filt_lats[i] = np.mean(lats[i-left_w:i+right_w])
            if not filt_lats[i]:
                print(f'lat[{i}] is empty') 
            filt_lons[i] = np.mean(lons[i-left_w:i+right_w])
            filt_ve[i] = np.mean(corr_ve[i-left_w:i+right_w])
            filt_vn[i] = np.mean(corr_vn[i-left_w:i+right_w])
        df.loc[indices, 'filt_lat'] = filt_lats
        df.loc[indices, 'filt_lon'] = filt_lons
        df.loc[indices, 'filt_ve'] = filt_ve
        df.loc[indices, 'filt_vn'] = filt_vn
    return df

In [15]:
fpath = 'drifters/'
fnames = ['buoydata_1_5000.dat', 'buoydata_5001_10000.dat', 'buoydata_10001_15000.dat','buoydata_15001_dec21.dat']    
    
headers = ['id', 'mm', 'dd', 'yy', 'lat', 'lon', 'temp', 've', 'vn', 'spd', 'var_lat', 'var_lon', 'var_temp']
df_d = read_drifters_to_df(fpath, fnames[0], headers)
df_d = df_d.drop(df_d.columns[[6,10,11,12]], axis=1)
df_d = add_hours_column(df_d)
# df_d = df_d.head(10)

In [18]:
df_d = df_d[df_d['yy']>=1993]
print(df_d)

              id  mm    dd    yy     lat      lon     ve      vn     spd  \
517363   7711163   1  1.00  1993  22.032  210.970 -1.861   0.478   1.921   
517364   7711163   1  1.25  1993  22.029  210.966 -1.998  -2.366   3.097   
517365   7711163   1  1.50  1993  22.023  210.962 -1.404  -3.711   3.967   
517366   7711163   1  1.75  1993  22.015  210.960 -0.529  -4.593   4.623   
517367   7711163   1  2.00  1993  22.005  210.960  0.611  -5.224   5.260   
...          ...  ..   ...   ...     ...      ...    ...     ...     ...   
8334588  9815710   3  8.25  1999  12.842   61.420 -6.746  12.206  13.946   
8334589  9815710   3  8.50  1999  12.872   61.388 -3.180  12.852  13.239   
8334590  9815710   3  8.75  1999  12.892   61.408  5.135  10.721  11.887   
8334591  9815710   3  9.00  1999  12.914   61.408  3.649   8.132   8.914   
8334592  9815710   3  9.25  1999  12.924   61.422  0.824   3.329   3.429   

              hrs  
517363   815232.0  
517364   815238.0  
517365   815244.0  
517366 

In [19]:
df_d = correct_velocities_wind_slip(df_d)

[1993, 1994, 1995, 1996, 1997, 1998, 1999, 2000, 2001, 2002, 2003, 2004, 2005, 2006]
1993
D:/era5/download_1993.nc
1994
D:/era5/download_1994.nc
1995
D:/era5/download_1995.nc
1996
D:/era5/download_1996.nc
1997
D:/era5/download_1997.nc
1998
D:/era5/download_1998.nc
1999
D:/era5/download_1999.nc
2000
D:/era5/download_2000.nc
2001
D:/era5/download_2001.nc
2002
D:/era5/download_2002.nc
2003
D:/era5/download_2003.nc
2004
D:/era5/download_2004.nc
2005
D:/era5/download_2005.nc
2006
D:/era5/download_2006.nc


In [20]:
print(df_d)
df_d.to_csv('tmp_df_d.csv')

              id  mm    dd    yy     lat      lon     ve      vn     spd  \
517363   7711163   1  1.00  1993  22.032  210.970 -1.861   0.478   1.921   
517364   7711163   1  1.25  1993  22.029  210.966 -1.998  -2.366   3.097   
517365   7711163   1  1.50  1993  22.023  210.962 -1.404  -3.711   3.967   
517366   7711163   1  1.75  1993  22.015  210.960 -0.529  -4.593   4.623   
517367   7711163   1  2.00  1993  22.005  210.960  0.611  -5.224   5.260   
...          ...  ..   ...   ...     ...      ...    ...     ...     ...   
8334588  9815710   3  8.25  1999  12.842   61.420 -6.746  12.206  13.946   
8334589  9815710   3  8.50  1999  12.872   61.388 -3.180  12.852  13.239   
8334590  9815710   3  8.75  1999  12.892   61.408  5.135  10.721  11.887   
8334591  9815710   3  9.00  1999  12.914   61.408  3.649   8.132   8.914   
8334592  9815710   3  9.25  1999  12.924   61.422  0.824   3.329   3.429   

              hrs   corr_ve    corr_vn  wind_u10  wind_v10  
517363   815232.0 -1.70582

In [21]:
df_filt = filter_inertial_motion(df_d)
df_filt.to_csv('tmp_df_filt.csv')

C:\Users\oa18724\Anaconda3\envs\dl_env\lib\site-packages\numpy\core\fromnumeric.py:3432: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
C:\Users\oa18724\Anaconda3\envs\dl_env\lib\site-packages\numpy\core\_methods.py:190: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


In [19]:
df_filt2 = pd.read_csv('tmp_df_filt.csv')
print(df_filt2)

         Unnamed: 0       id  mm    dd    yy     lat      lon     ve      vn  \
0            517363  7711163   1  1.00  1993  22.032  210.970 -1.861   0.478   
1            517364  7711163   1  1.25  1993  22.029  210.966 -1.998  -2.366   
2            517365  7711163   1  1.50  1993  22.023  210.962 -1.404  -3.711   
3            517366  7711163   1  1.75  1993  22.015  210.960 -0.529  -4.593   
4            517367  7711163   1  2.00  1993  22.005  210.960  0.611  -5.224   
...             ...      ...  ..   ...   ...     ...      ...    ...     ...   
6479054     8334588  9815710   3  8.25  1999  12.842   61.420 -6.746  12.206   
6479055     8334589  9815710   3  8.50  1999  12.872   61.388 -3.180  12.852   
6479056     8334590  9815710   3  8.75  1999  12.892   61.408  5.135  10.721   
6479057     8334591  9815710   3  9.00  1999  12.914   61.408  3.649   8.132   
6479058     8334592  9815710   3  9.25  1999  12.924   61.422  0.824   3.329   

            spd       hrs   corr_ve    

In [20]:
nan_ind = np.where(df_filt2['filt_lat'].isna())[0]
print(print(nan_ind))
# print(df_filt.loc[1148263, :])

[1148263 1739173 2326410]
None


In [21]:
# ammend according to above
df_filt3 = df_filt2.drop([df_filt2.index[1148263], df_filt2.index[1739173], df_filt2.index[2326410]])
nan_ind = np.where(df_filt3['filt_lat'].isna())[0]
print(print(nan_ind))

[]
None


In [26]:
# def compute_geostrophic_anomalies(df):
#     df = df.copy()
#     mnths = sorted(df['mm'].unique())
#     yrs = sorted(df['yy'].unique())
    
#     print(yrs)
#     for yr in yrs:
#         print(yr)
#         f_path = f'D:/adt_calculations/SSH/duacs/cmems_obs-sl_glo_phy-ssh_my_allsat-l4-duacs-0.25deg_P1M-m/{yr}'
#         if os.path.exists(f_path):
#             for m in mnths:
#                 fpath = os.path.join(f_path, f'dt_global_allsat_msla_h_y{yr}_m{str(m).zfill(2)}.nc')
#                 ssh_dataset = nc.Dataset(fpath)
#                 df = interpolate_sla(df, ssh_dataset)
#         else:
#             print(f'{yr} ssh file does not exist')
#     return df
# # times = ssh_dataset.variables['time'][:]
# # u10, v10 = ssh_dataset.variables['u10'], ssh_dataset.variables['v10']
# # lats, lons = ssh_dataset.variables['latitude'][:], ssh_dataset.variables['longitude'][:]
# # for i, time in enumerate(times):
# #     f_u10 = interpolate.interp2d(lons, lats, u10[i], kind='cubic')
# #     f_v10 = interpolate.interp2d(lons, lats, v10[i], kind='cubic')

In [27]:
# def interpolate_sla(df, data):
#     times = data.variables['time'][:]
#     sla = data.variables['sla']
#     lats, lons = data.variables['latitude'][:], data.variables['longitude'][:]
#     for i, time in enumerate(times):
#         print(time)
#         f_interp = interpolate.interp2d(lons, lats, sla[i], kind='cubic')
# #         df_t = df.loc[(df["mm"]==int()) & df["dd"]==]
# #         df_t = df.loc[df["hrs"]==time]
# #         indices = df.index[df["hrs"]==time]
# #         any_true = np.any(df["hrs"]==time)
# #         if any_true:
#             # print(i, f"there was a match!!!")
#         sla_new = df_t.apply(lambda x: f_interp(x['lon'], x['lat'])[0], axis=1)
#         df.loc[indices,'sla'] = sla_new
#     return df

In [28]:
# df_filt2 = compute_geostrophic_anomalies(df_filt2)
# print(df_filt2)

In [49]:
# should be renamed
def compute_anom_vel_of_box(df, box_size=5):
    df = df.copy()
    df[df.columns[0]].count()
    df['vn_anom'] = 0
    df['ve_anom'] = 0
    lon_range = np.arange(0, 360, box_size)
    lat_range = np.arange(-90, 90, box_size)
#     print('lon_range:', lon_range, 'lat_range:', lat_range)
    
    for lon in lon_range:
        for lat in lat_range:
#             print(lon, lat)
            indices = (df['filt_lon']>=lon) & (df['filt_lon']<lon+5) & (df['filt_lat']>=lat) & (df['filt_lat']<lat+5)
            box = df.loc[indices]
#             print('*', box)
#             exit()
            if not box.empty:
                mean_vn = np.mean(box['filt_vn'].to_numpy())
                mean_ve = np.mean(box['filt_ve'].to_numpy())
                print('>>>>', mean_vn, mean_ve)
                df.loc[indices, 'vn_anom'] = box['filt_vn'] - mean_vn
                df.loc[indices, 've_anom'] = box['filt_ve'] - mean_ve
            box = df.loc[indices]
            print('**', box)
    return df

In [50]:
df_filt_anom = compute_anom_vel_of_box(df_filt3)
df_filt_anom.to_csv('tmp_df_filt_anom.csv')

         Unnamed: 0       id  mm    dd    yy     lat      lon     ve      vn  \
0            517363  7711163   1  1.00  1993  22.032  210.970 -1.861   0.478   
1            517364  7711163   1  1.25  1993  22.029  210.966 -1.998  -2.366   
2            517365  7711163   1  1.50  1993  22.023  210.962 -1.404  -3.711   
3            517366  7711163   1  1.75  1993  22.015  210.960 -0.529  -4.593   
4            517367  7711163   1  2.00  1993  22.005  210.960  0.611  -5.224   
...             ...      ...  ..   ...   ...     ...      ...    ...     ...   
6479054     8334588  9815710   3  8.25  1999  12.842   61.420 -6.746  12.206   
6479055     8334589  9815710   3  8.50  1999  12.872   61.388 -3.180  12.852   
6479056     8334590  9815710   3  8.75  1999  12.892   61.408  5.135  10.721   
6479057     8334591  9815710   3  9.00  1999  12.914   61.408  3.649   8.132   
6479058     8334592  9815710   3  9.25  1999  12.924   61.422  0.824   3.329   

            spd       hrs   corr_ve    

*          Unnamed: 0       id  mm     dd    yy     lat    lon      ve      vn  \
2103632     3783061  9422037   4  30.25  1995 -37.371  0.473  11.255  14.755   
2103633     3783062  9422037   4  30.50  1995 -37.342  0.492  22.068  20.776   
2103634     3783063  9422037   4  30.75  1995 -37.290  0.580  28.833  21.268   
2103635     3783064  9422037   5   1.00  1995 -37.259  0.633  16.502  10.898   
2103636     3783065  9422037   5   1.25  1995 -37.248  0.660  23.374   4.894   
...             ...      ...  ..    ...   ...     ...    ...     ...     ...   
6476616     8332144  9714830   4  16.50  2001 -38.091  4.381  50.114 -19.267   
6476617     8332145  9714830   4  16.75  2001 -38.129  4.506  48.865 -25.956   
6476618     8332146  9714830   4  17.00  2001 -38.191  4.622  57.145 -28.472   
6476619     8332147  9714830   4  17.25  2001 -38.239  4.788  61.377 -30.715   
6476620     8332148  9714830   4  17.50  2001 -38.311  4.925  66.709 -35.784   

            spd  ...    corr_ve    co

*          Unnamed: 0       id  mm     dd    yy    lat    lon      ve      vn  \
4656896     6434617  9701611   4  21.25  1999 -5.047  2.555  -2.577 -26.545   
4656897     6434618  9701611   4  21.50  1999 -5.099  2.550  -2.538 -26.528   
4656898     6434619  9701611   4  21.75  1999 -5.151  2.546  -2.506 -26.497   
4656899     6434620  9701611   4  22.00  1999 -5.202  2.541  -2.428 -26.451   
4656900     6434621  9701611   4  22.25  1999 -5.254  2.536  -2.326 -26.392   
...             ...      ...  ..    ...   ...    ...    ...     ...     ...   
4657041     6434762  9701611   5  27.50  1999 -5.251  0.418 -32.507  -1.157   
4657042     6434763  9701611   5  27.75  1999 -5.254  0.351 -36.446  -0.982   
4657043     6434764  9701611   5  28.00  1999 -5.255  0.276 -39.226  -1.066   
4657044     6434765  9701611   5  28.25  1999 -5.258  0.198 -39.821  -1.572   
4657045     6434766  9701611   5  28.50  1999 -5.261  0.120 -39.734  -2.477   

            spd  ...    corr_ve    corr_vn  wind_

[0 rows x 21 columns]
* Empty DataFrame
Columns: [Unnamed: 0, id, mm, dd, yy, lat, lon, ve, vn, spd, hrs, corr_ve, corr_vn, wind_u10, wind_v10, filt_lat, filt_lon, filt_ve, filt_vn, vn_anom, ve_anom]
Index: []

[0 rows x 21 columns]
* Empty DataFrame
Columns: [Unnamed: 0, id, mm, dd, yy, lat, lon, ve, vn, spd, hrs, corr_ve, corr_vn, wind_u10, wind_v10, filt_lat, filt_lon, filt_ve, filt_vn, vn_anom, ve_anom]
Index: []

[0 rows x 21 columns]
* Empty DataFrame
Columns: [Unnamed: 0, id, mm, dd, yy, lat, lon, ve, vn, spd, hrs, corr_ve, corr_vn, wind_u10, wind_v10, filt_lat, filt_lon, filt_ve, filt_vn, vn_anom, ve_anom]
Index: []

[0 rows x 21 columns]
* Empty DataFrame
Columns: [Unnamed: 0, id, mm, dd, yy, lat, lon, ve, vn, spd, hrs, corr_ve, corr_vn, wind_u10, wind_v10, filt_lat, filt_lon, filt_ve, filt_vn, vn_anom, ve_anom]
Index: []

[0 rows x 21 columns]
* Empty DataFrame
Columns: [Unnamed: 0, id, mm, dd, yy, lat, lon, ve, vn, spd, hrs, corr_ve, corr_vn, wind_u10, wind_v10, filt_lat, fi

* Empty DataFrame
Columns: [Unnamed: 0, id, mm, dd, yy, lat, lon, ve, vn, spd, hrs, corr_ve, corr_vn, wind_u10, wind_v10, filt_lat, filt_lon, filt_ve, filt_vn, vn_anom, ve_anom]
Index: []

[0 rows x 21 columns]
* Empty DataFrame
Columns: [Unnamed: 0, id, mm, dd, yy, lat, lon, ve, vn, spd, hrs, corr_ve, corr_vn, wind_u10, wind_v10, filt_lat, filt_lon, filt_ve, filt_vn, vn_anom, ve_anom]
Index: []

[0 rows x 21 columns]
* Empty DataFrame
Columns: [Unnamed: 0, id, mm, dd, yy, lat, lon, ve, vn, spd, hrs, corr_ve, corr_vn, wind_u10, wind_v10, filt_lat, filt_lon, filt_ve, filt_vn, vn_anom, ve_anom]
Index: []

[0 rows x 21 columns]
* Empty DataFrame
Columns: [Unnamed: 0, id, mm, dd, yy, lat, lon, ve, vn, spd, hrs, corr_ve, corr_vn, wind_u10, wind_v10, filt_lat, filt_lon, filt_ve, filt_vn, vn_anom, ve_anom]
Index: []

[0 rows x 21 columns]
* Empty DataFrame
Columns: [Unnamed: 0, id, mm, dd, yy, lat, lon, ve, vn, spd, hrs, corr_ve, corr_vn, wind_u10, wind_v10, filt_lat, filt_lon, filt_ve, filt_

...

*          Unnamed: 0       id  mm     dd    yy     lat      lon      ve  \
1925994     3604459  7722591   4   9.75  1995 -47.000  354.878  35.580   
1925995     3604460  7722591   4  10.00  1995 -47.056  355.007  38.768   
1925996     3604461  7722591   4  10.25  1995 -47.067  355.099  29.623   
1925998     3604463  7722591   4  10.75  1995 -47.162  355.312  52.413   
1925999     3604464  7722591   4  11.00  1995 -47.177  355.474  62.459   
...             ...      ...  ..    ...   ...     ...      ...     ...   
6464852     8320191  9714825  12  26.25  1999 -45.137  357.381  11.787   
6464853     8320192  9714825  12  26.50  1999 -45.128  357.455  27.010   
6464854     8320193  9714825  12  26.75  1999 -45.077  357.530  15.001   
6464855     8320194  9714825  12  27.00  1999 -45.068  357.537  18.885   
6464856     8320195  9714825  12  27.25  1999 -45.027  357.633  17.636   

             vn     spd  ...    corr_ve    corr_vn   wind_u10  wind_v10  \
1925994 -30.532  46.885  ...  35.2

>>>> 0.8489501394547077 0.15829475414274807
*          Unnamed: 0       id  mm     dd    yy     lat      lon      ve  \
1953105     3631871  9421177   7  27.00  1997 -26.143  359.873 -24.171   
1953106     3631872  9421177   7  27.25  1997 -26.141  359.821 -24.152   
1953107     3631873  9421177   7  27.50  1997 -26.139  359.769 -23.836   
1953108     3631874  9421177   7  27.75  1997 -26.138  359.718 -23.103   
1953109     3631875  9421177   7  28.00  1997 -26.138  359.669 -21.269   
...             ...      ...  ..    ...   ...     ...      ...     ...   
6460938     8316269  9812234   4   7.75  2001 -27.665  359.853  -2.421   
6460939     8316270  9812234   4   8.00  2001 -27.663  359.866   7.133   
6460940     8316271  9812234   4   8.25  2001 -27.658  359.884   9.106   
6460941     8316272  9812234   4   8.50  2001 -27.641  359.906  10.674   
6460942     8316273  9812234   4   8.75  2001 -27.622  359.931  11.282   

             vn     spd  ...    corr_ve    corr_vn  wind_u10  win

*          Unnamed: 0       id  mm     dd    yy    lat      lon      ve      vn  \
4654571     6432292  9701611   9  17.00  1997  3.043  355.290  84.459 -32.276   
4654572     6432293  9701611   9  17.25  1997  2.989  355.457  86.276 -25.184   
4654573     6432294  9701611   9  17.50  1997  2.945  355.625  86.532 -21.619   
4654574     6432295  9701611   9  17.75  1997  2.904  355.793  85.002 -19.439   
4654575     6432296  9701611   9  18.00  1997  2.869  355.956  78.978 -14.382   
...             ...      ...  ..    ...   ...    ...      ...     ...     ...   
6363373     8218540  9824557   9   3.50  1999  1.852  359.671  33.276 -20.427   
6363374     8218541  9824557   9   3.75  1999  1.812  359.737  32.904 -19.558   
6363375     8218542  9824557   9   4.00  1999  1.776  359.799  35.135 -18.110   
6363376     8218543  9824557   9   4.25  1999  1.741  359.873  34.129 -14.601   
6363377     8218544  9824557   9   4.50  1999  1.719  359.931  28.514 -11.343   

            spd  ...    c

*          Unnamed: 0       id  mm     dd    yy     lat      lon     ve      vn  \
3069132     4815772  9423533   9  30.50  1998  66.476  359.819 -1.322  26.671   
3069133     4815773  9423533   9  30.75  1998  66.528  359.813 -0.934  26.882   
3069134     4815774  9423533  10   1.00  1998  66.580  359.809 -0.596  26.833   
3069135     4815775  9423533  10   1.25  1998  66.632  359.807 -0.226  26.514   
3069136     4815776  9423533  10   1.50  1998  66.683  359.807  0.346  25.864   
...             ...      ...  ..    ...   ...     ...      ...    ...     ...   
6187727     8040301  9914698   9  15.25  2000  69.072  358.249 -0.688   4.136   
6187728     8040302  9914698   9  15.50  2000  69.080  358.245 -0.665   4.092   
6187729     8040303  9914698   9  15.75  2000  69.088  358.241 -0.650   4.034   
6187730     8040304  9914698   9  16.00  2000  69.095  358.238 -0.637   3.956   
6187731     8040305  9914698   9  16.25  2000  69.103  358.234 -0.629   3.854   

            spd  ...   co

[0 rows x 21 columns]
* Empty DataFrame
Columns: [Unnamed: 0, id, mm, dd, yy, lat, lon, ve, vn, spd, hrs, corr_ve, corr_vn, wind_u10, wind_v10, filt_lat, filt_lon, filt_ve, filt_vn, vn_anom, ve_anom]
Index: []

[0 rows x 21 columns]


In [57]:
# df_filt_anom = pd.read_csv('tmp_df_filt_anom.csv')
print(df_filt_anom.loc[df_filt_anom['ve_anom']==0])
# print(df_filt_anom)

         Unnamed: 0       id  mm     dd    yy     lat      lon      ve  \
778656      2272060  7700475   1  21.00  1994  53.408  329.768  13.338   
778660      2272064  7700475   1  22.00  1994  53.406  330.017  19.552   
779582      2272986  7700475   9   9.50  1994  59.638    1.320 -12.078   
779583      2272987  7700475   9   9.75  1994  59.666    1.274 -12.024   
779585      2272989  7700475   9  10.25  1994  59.721    1.182 -11.877   
...             ...      ...  ..    ...   ...     ...      ...     ...   
5789406     7612438  9215919   2  17.50  1994  69.114    5.003  18.407   
5928432     7777623  9619716  11  15.50  1999  -0.310  359.679 -36.622   
6346596     8201731  9912367   3  13.75  2000 -22.005    4.198  -3.374   
6349717     8204856  9914471   4   2.00  2000 -18.844  353.573 -15.829   
6349809     8204948  9914471   4  25.00  2000 -18.846  351.526  -2.620   

             vn     spd  ...    corr_ve    corr_vn   wind_u10  wind_v10  \
778656  -11.960  17.915  ...  12.136

In [58]:
index = df_filt_anom['filt_lat'].index[df_filt_anom['filt_lat'].apply(np.isnan)]
print(index)

Int64Index([], dtype='int64')


In [77]:
def compute_norm_wind_stress(df):
    df = df.copy()
    c_d_u = 0.0027 * 1/df['wind_u10'] + 0.000142 + 0.0000764 * df['wind_u10'].abs()
    c_d_v = 0.0027 * 1/df['wind_v10'] + 0.000142 + 0.0000764 * df['wind_v10'].abs()
    rho = 1.225
    tau_u10 = c_d_u * rho * df['wind_u10'] * df['wind_u10'].abs()
    tau_v10 = c_d_v * rho * df['wind_v10'] * df['wind_v10'].abs()
    df['tau_u10'] = tau_u10
    df['tau_v10'] = tau_v10
    f = 2*omega*np.sin(df['filt_lat'])
    df['norm_tu10'] = tau_u10/((f*tau_u10).abs())**(1/2)
    df['norm_tv10'] = tau_v10/((f*tau_v10).abs())**(1/2)
    return df

In [76]:
def compute_anom_wind_stress(df, box_size=5):
    df = df.copy()
    df['tu10_anom'] = 0
    df['tv10_anom'] = 0
    lon_range = np.arange(0, 360, box_size)
    lat_range = np.arange(-90, 90, box_size)
    print('lon_range:', lon_range, 'lat_range:', lat_range)
    
    for lon in lon_range:
        for lat in lat_range:
            indices = (df['filt_lon']>=lon) & (df['filt_lon']<lon+5) & (df['filt_lat']>=lat) & (df['filt_lat']<lat+5)
            box = df.loc[indices]
            if not box.empty:
                mean_tu = np.mean(box['norm_tu10'].to_numpy())
                mean_tv = np.mean(box['norm_tv10'].to_numpy())
                df.loc[indices, 'tu10_anom'] = box['norm_tu10'] - mean_tu
                df.loc[indices, 'tv10_anom'] = box['norm_tv10'] - mean_tv
    return df

In [75]:
# df_filt_anom_tau = compute_norm_wind_stress(df_filt_anom)
# df_filt_anom_tau = compute_anom_wind_stress(df_filt_anom_tau)
print(df_filt_anom_tau)
df_filt_anom_tau.to_csv('tmp_df_filt_anom_tau.csv')

         Unnamed: 0       id  mm    dd    yy     lat      lon     ve      vn  \
0            517363  7711163   1  1.00  1993  22.032  210.970 -1.861   0.478   
1            517364  7711163   1  1.25  1993  22.029  210.966 -1.998  -2.366   
2            517365  7711163   1  1.50  1993  22.023  210.962 -1.404  -3.711   
3            517366  7711163   1  1.75  1993  22.015  210.960 -0.529  -4.593   
4            517367  7711163   1  2.00  1993  22.005  210.960  0.611  -5.224   
...             ...      ...  ..   ...   ...     ...      ...    ...     ...   
6479054     8334588  9815710   3  8.25  1999  12.842   61.420 -6.746  12.206   
6479055     8334589  9815710   3  8.50  1999  12.872   61.388 -3.180  12.852   
6479056     8334590  9815710   3  8.75  1999  12.892   61.408  5.135  10.721   
6479057     8334591  9815710   3  9.00  1999  12.914   61.408  3.649   8.132   
6479058     8334592  9815710   3  9.25  1999  12.924   61.422  0.824   3.329   

            spd  ...   filt_lat    filt

In [66]:
print(df_filt_anom_tau.loc[df_filt_anom_tau['norm_tu10'].apply(np.isnan)])
index = df_filt_anom_tau['norm_tu10'].index[df_filt_anom_tau['norm_tu10'].apply(np.isnan)] 
print(len(index))

Empty DataFrame
Columns: [Unnamed: 0, id, mm, dd, yy, lat, lon, ve, vn, spd, hrs, corr_ve, corr_vn, wind_u10, wind_v10, filt_lat, filt_lon, filt_ve, filt_vn, vn_anom, ve_anom, tau_u10, tau_v10, norm_tu10, norm_tv10, tu10_anom, tv10_anom]
Index: []

[0 rows x 27 columns]
0


In [67]:
def load_ssh_data(df):
    df = df.copy()
    df['sla'] = 0
#     yrs = sorted(df['yy'].unique())
    mnths = sorted(df['mm'].unique())
    days = sorted(df['dd'].unique())
    yrs = np.arange(1993,2022)
#     yrs = [1999]

    for yr in yrs:
        for mnth in mnths:
#             print(yr, mnth)
            for day in days:
#                 print(day, round(day), mnth, yr)
                fpath = f'D:/ssh_daily/ssh_{yr}/dt_global_twosat_phy_l4_{yr}{str(mnth).zfill(2)}{str(round(day)).zfill(2)}_vDT2021.nc'
                if os.path.exists(fpath):
                    ssh_dataset = nc.Dataset(fpath)
                    sla = ssh_dataset['sla'][0]
                    lons, lats = ssh_dataset['longitude'], ssh_dataset['latitude']
                    indices = (df['yy']==yr) & (df['mm']==mnth) & (df['dd']==day)
                    df_t = df.loc[indices]
                    f = interpolate.interp2d(lons, lats, sla, kind='cubic')
                    
                    ssh_new = df_t.apply(lambda x: f(x['lon'], x['lat'])[0], axis=1)
                    df.loc[indices,'sla'] = ssh_new
                        
                else:
                    print(f'yr: {yr}, mnth: {mnth}, day: {day} ssh file does not exist')
    return df

In [68]:
df_cmplt = load_ssh_data(df_filt_anom_tau)
df_cmplt.to_csv('tmp_df_cmplt.csv')
print(df_cmplt)

yr: 1993, mnth: 1, day: 31.5 ssh file does not exist
yr: 1993, mnth: 1, day: 31.75 ssh file does not exist
yr: 1993, mnth: 2, day: 28.75 ssh file does not exist
yr: 1993, mnth: 2, day: 29.0 ssh file does not exist
yr: 1993, mnth: 2, day: 29.25 ssh file does not exist
yr: 1993, mnth: 2, day: 29.5 ssh file does not exist
yr: 1993, mnth: 2, day: 29.75 ssh file does not exist
yr: 1993, mnth: 2, day: 30.0 ssh file does not exist
yr: 1993, mnth: 2, day: 30.25 ssh file does not exist
yr: 1993, mnth: 2, day: 30.5 ssh file does not exist
yr: 1993, mnth: 2, day: 30.75 ssh file does not exist
yr: 1993, mnth: 2, day: 31.0 ssh file does not exist
yr: 1993, mnth: 2, day: 31.25 ssh file does not exist
yr: 1993, mnth: 2, day: 31.5 ssh file does not exist
yr: 1993, mnth: 2, day: 31.75 ssh file does not exist
yr: 1993, mnth: 3, day: 31.5 ssh file does not exist
yr: 1993, mnth: 3, day: 31.75 ssh file does not exist
yr: 1993, mnth: 4, day: 30.75 ssh file does not exist
yr: 1993, mnth: 4, day: 31.0 ssh fil

yr: 1996, mnth: 3, day: 31.5 ssh file does not exist
yr: 1996, mnth: 3, day: 31.75 ssh file does not exist
yr: 1996, mnth: 4, day: 30.75 ssh file does not exist
yr: 1996, mnth: 4, day: 31.0 ssh file does not exist
yr: 1996, mnth: 4, day: 31.25 ssh file does not exist
yr: 1996, mnth: 4, day: 31.5 ssh file does not exist
yr: 1996, mnth: 4, day: 31.75 ssh file does not exist
yr: 1996, mnth: 5, day: 31.5 ssh file does not exist
yr: 1996, mnth: 5, day: 31.75 ssh file does not exist
yr: 1996, mnth: 6, day: 30.75 ssh file does not exist
yr: 1996, mnth: 6, day: 31.0 ssh file does not exist
yr: 1996, mnth: 6, day: 31.25 ssh file does not exist
yr: 1996, mnth: 6, day: 31.5 ssh file does not exist
yr: 1996, mnth: 6, day: 31.75 ssh file does not exist
yr: 1996, mnth: 7, day: 31.5 ssh file does not exist
yr: 1996, mnth: 7, day: 31.75 ssh file does not exist
yr: 1996, mnth: 8, day: 31.5 ssh file does not exist
yr: 1996, mnth: 8, day: 31.75 ssh file does not exist
yr: 1996, mnth: 9, day: 30.75 ssh fi

yr: 1999, mnth: 7, day: 31.5 ssh file does not exist
yr: 1999, mnth: 7, day: 31.75 ssh file does not exist
yr: 1999, mnth: 8, day: 31.5 ssh file does not exist
yr: 1999, mnth: 8, day: 31.75 ssh file does not exist
yr: 1999, mnth: 9, day: 30.75 ssh file does not exist
yr: 1999, mnth: 9, day: 31.0 ssh file does not exist
yr: 1999, mnth: 9, day: 31.25 ssh file does not exist
yr: 1999, mnth: 9, day: 31.5 ssh file does not exist
yr: 1999, mnth: 9, day: 31.75 ssh file does not exist
yr: 1999, mnth: 10, day: 31.5 ssh file does not exist
yr: 1999, mnth: 10, day: 31.75 ssh file does not exist
yr: 1999, mnth: 11, day: 30.75 ssh file does not exist
yr: 1999, mnth: 11, day: 31.0 ssh file does not exist
yr: 1999, mnth: 11, day: 31.25 ssh file does not exist
yr: 1999, mnth: 11, day: 31.5 ssh file does not exist
yr: 1999, mnth: 11, day: 31.75 ssh file does not exist
yr: 1999, mnth: 12, day: 31.5 ssh file does not exist
yr: 1999, mnth: 12, day: 31.75 ssh file does not exist
yr: 2000, mnth: 1, day: 31.

yr: 2002, mnth: 12, day: 31.5 ssh file does not exist
yr: 2002, mnth: 12, day: 31.75 ssh file does not exist
yr: 2003, mnth: 1, day: 31.5 ssh file does not exist
yr: 2003, mnth: 1, day: 31.75 ssh file does not exist
yr: 2003, mnth: 2, day: 28.75 ssh file does not exist
yr: 2003, mnth: 2, day: 29.0 ssh file does not exist
yr: 2003, mnth: 2, day: 29.25 ssh file does not exist
yr: 2003, mnth: 2, day: 29.5 ssh file does not exist
yr: 2003, mnth: 2, day: 29.75 ssh file does not exist
yr: 2003, mnth: 2, day: 30.0 ssh file does not exist
yr: 2003, mnth: 2, day: 30.25 ssh file does not exist
yr: 2003, mnth: 2, day: 30.5 ssh file does not exist
yr: 2003, mnth: 2, day: 30.75 ssh file does not exist
yr: 2003, mnth: 2, day: 31.0 ssh file does not exist
yr: 2003, mnth: 2, day: 31.25 ssh file does not exist
yr: 2003, mnth: 2, day: 31.5 ssh file does not exist
yr: 2003, mnth: 2, day: 31.75 ssh file does not exist
yr: 2003, mnth: 3, day: 31.5 ssh file does not exist
yr: 2003, mnth: 3, day: 31.75 ssh f

yr: 2006, mnth: 3, day: 31.5 ssh file does not exist
yr: 2006, mnth: 3, day: 31.75 ssh file does not exist
yr: 2006, mnth: 4, day: 30.75 ssh file does not exist
yr: 2006, mnth: 4, day: 31.0 ssh file does not exist
yr: 2006, mnth: 4, day: 31.25 ssh file does not exist
yr: 2006, mnth: 4, day: 31.5 ssh file does not exist
yr: 2006, mnth: 4, day: 31.75 ssh file does not exist
yr: 2006, mnth: 5, day: 31.5 ssh file does not exist
yr: 2006, mnth: 5, day: 31.75 ssh file does not exist
yr: 2006, mnth: 6, day: 30.75 ssh file does not exist
yr: 2006, mnth: 6, day: 31.0 ssh file does not exist
yr: 2006, mnth: 6, day: 31.25 ssh file does not exist
yr: 2006, mnth: 6, day: 31.5 ssh file does not exist
yr: 2006, mnth: 6, day: 31.75 ssh file does not exist
yr: 2006, mnth: 7, day: 31.5 ssh file does not exist
yr: 2006, mnth: 7, day: 31.75 ssh file does not exist
yr: 2006, mnth: 8, day: 31.5 ssh file does not exist
yr: 2006, mnth: 8, day: 31.75 ssh file does not exist
yr: 2006, mnth: 9, day: 30.75 ssh fi

yr: 2009, mnth: 8, day: 31.5 ssh file does not exist
yr: 2009, mnth: 8, day: 31.75 ssh file does not exist
yr: 2009, mnth: 9, day: 30.75 ssh file does not exist
yr: 2009, mnth: 9, day: 31.0 ssh file does not exist
yr: 2009, mnth: 9, day: 31.25 ssh file does not exist
yr: 2009, mnth: 9, day: 31.5 ssh file does not exist
yr: 2009, mnth: 9, day: 31.75 ssh file does not exist
yr: 2009, mnth: 10, day: 31.5 ssh file does not exist
yr: 2009, mnth: 10, day: 31.75 ssh file does not exist
yr: 2009, mnth: 11, day: 30.75 ssh file does not exist
yr: 2009, mnth: 11, day: 31.0 ssh file does not exist
yr: 2009, mnth: 11, day: 31.25 ssh file does not exist
yr: 2009, mnth: 11, day: 31.5 ssh file does not exist
yr: 2009, mnth: 11, day: 31.75 ssh file does not exist
yr: 2009, mnth: 12, day: 31.5 ssh file does not exist
yr: 2009, mnth: 12, day: 31.75 ssh file does not exist
yr: 2010, mnth: 1, day: 31.5 ssh file does not exist
yr: 2010, mnth: 1, day: 31.75 ssh file does not exist
yr: 2010, mnth: 2, day: 28.

yr: 2013, mnth: 1, day: 31.5 ssh file does not exist
yr: 2013, mnth: 1, day: 31.75 ssh file does not exist
yr: 2013, mnth: 2, day: 28.75 ssh file does not exist
yr: 2013, mnth: 2, day: 29.0 ssh file does not exist
yr: 2013, mnth: 2, day: 29.25 ssh file does not exist
yr: 2013, mnth: 2, day: 29.5 ssh file does not exist
yr: 2013, mnth: 2, day: 29.75 ssh file does not exist
yr: 2013, mnth: 2, day: 30.0 ssh file does not exist
yr: 2013, mnth: 2, day: 30.25 ssh file does not exist
yr: 2013, mnth: 2, day: 30.5 ssh file does not exist
yr: 2013, mnth: 2, day: 30.75 ssh file does not exist
yr: 2013, mnth: 2, day: 31.0 ssh file does not exist
yr: 2013, mnth: 2, day: 31.25 ssh file does not exist
yr: 2013, mnth: 2, day: 31.5 ssh file does not exist
yr: 2013, mnth: 2, day: 31.75 ssh file does not exist
yr: 2013, mnth: 3, day: 31.5 ssh file does not exist
yr: 2013, mnth: 3, day: 31.75 ssh file does not exist
yr: 2013, mnth: 4, day: 30.75 ssh file does not exist
yr: 2013, mnth: 4, day: 31.0 ssh fil

yr: 2016, mnth: 3, day: 31.5 ssh file does not exist
yr: 2016, mnth: 3, day: 31.75 ssh file does not exist
yr: 2016, mnth: 4, day: 30.75 ssh file does not exist
yr: 2016, mnth: 4, day: 31.0 ssh file does not exist
yr: 2016, mnth: 4, day: 31.25 ssh file does not exist
yr: 2016, mnth: 4, day: 31.5 ssh file does not exist
yr: 2016, mnth: 4, day: 31.75 ssh file does not exist
yr: 2016, mnth: 5, day: 31.5 ssh file does not exist
yr: 2016, mnth: 5, day: 31.75 ssh file does not exist
yr: 2016, mnth: 6, day: 30.75 ssh file does not exist
yr: 2016, mnth: 6, day: 31.0 ssh file does not exist
yr: 2016, mnth: 6, day: 31.25 ssh file does not exist
yr: 2016, mnth: 6, day: 31.5 ssh file does not exist
yr: 2016, mnth: 6, day: 31.75 ssh file does not exist
yr: 2016, mnth: 7, day: 31.5 ssh file does not exist
yr: 2016, mnth: 7, day: 31.75 ssh file does not exist
yr: 2016, mnth: 8, day: 31.5 ssh file does not exist
yr: 2016, mnth: 8, day: 31.75 ssh file does not exist
yr: 2016, mnth: 9, day: 30.75 ssh fi

yr: 2019, mnth: 7, day: 31.5 ssh file does not exist
yr: 2019, mnth: 7, day: 31.75 ssh file does not exist
yr: 2019, mnth: 8, day: 31.5 ssh file does not exist
yr: 2019, mnth: 8, day: 31.75 ssh file does not exist
yr: 2019, mnth: 9, day: 30.75 ssh file does not exist
yr: 2019, mnth: 9, day: 31.0 ssh file does not exist
yr: 2019, mnth: 9, day: 31.25 ssh file does not exist
yr: 2019, mnth: 9, day: 31.5 ssh file does not exist
yr: 2019, mnth: 9, day: 31.75 ssh file does not exist
yr: 2019, mnth: 10, day: 31.5 ssh file does not exist
yr: 2019, mnth: 10, day: 31.75 ssh file does not exist
yr: 2019, mnth: 11, day: 30.75 ssh file does not exist
yr: 2019, mnth: 11, day: 31.0 ssh file does not exist
yr: 2019, mnth: 11, day: 31.25 ssh file does not exist
yr: 2019, mnth: 11, day: 31.5 ssh file does not exist
yr: 2019, mnth: 11, day: 31.75 ssh file does not exist
yr: 2019, mnth: 12, day: 31.5 ssh file does not exist
yr: 2019, mnth: 12, day: 31.75 ssh file does not exist
yr: 2020, mnth: 1, day: 31.

In [91]:
import cmath
def cmplx_least_squares(df, box_size=5):
    df = df.copy()
    lon_range = np.arange(0, 360, box_size)
    lat_range = np.arange(-90, 90, box_size)
    print('lon_range:', lon_range, 'lat_range:', lat_range)
    hrs = sorted(df['hrs'].unique())
    all_b_theta = np.zeros(len(hrs))
    
    for i, hr in enumerate(hrs):
        indices = (df['hrs']==hr)
        df_t = df.loc[indices]
        b_theta = np.zeros((len(lon_range), len(lat_range)))
        for j, lon in enumerate(lon_range):
            for k, lat in enumerate(lat_range):
                indices = (df['filt_lon']>=lon) & (df['filt_lon']<lon+5) & (df['filt_lat']>=lat) & (df['filt_lat']<lat+5)
                box = df.loc[indices]
                if box[box.columns[0]].count()>=1000:
                    u_y = box['ve_anom']
                    v_y = box['vn_anom']
                    u_x = box['tu10_anom']
                    v_x = box['tv10_anom']
                    y = complex(u_y, v_y)
                    x = complex(u_x, v_x)
                    c = np.sum(np.conj(x)*y) / np.sum(x**2)
    #                 b = cmath.polar(c)[0]
    #                 theta = cmath.polar(c)[1]
                    b_theta[j,k] = c
            all_b_theta[i] = b_theta
#             else:
#                 for boxes less than 1000
    
    return all_b_theta

    # Loop through boxes of 1000
    # Least squares
    # Save b and theta per box

# def compute_anom_wind_stress(df, box_size=5):
#     df = df.copy()
#     df['tu10_anom'] = 0
#     df['tv10_anom'] = 0
#     lon_range = np.arange(0, 360, box_size)
#     lat_range = np.arange(-90, 90, box_size)
#     print('lon_range:', lon_range, 'lat_range:', lat_range)
    
#     for lon in lon_range:
#         for lat in lat_range:
#             indices = (df['filt_lon']>=lon) & (df['filt_lon']<lon+5) & (df['filt_lat']>=lat) & (df['filt_lat']<lat+5)
#             box = df.loc[indices]
#             if box[box.columns[0]].count()>=1000:
#                 mean_tu = np.mean(box['norm_tu10'].to_numpy())
#                 mean_tv = np.mean(box['norm_tv10'].to_numpy())
#                 df.loc[indices, 'tu10_anom'] = box['norm_tu10'] - mean_tu
#                 df.loc[indices, 'tv10_anom'] = box['norm_tv10'] - mean_tv
#             else:
                
#     return df
    
    


In [92]:
all_b_theta = cmplx_least_squares(df_cmplt)

lon_range: [  0   5  10  15  20  25  30  35  40  45  50  55  60  65  70  75  80  85
  90  95 100 105 110 115 120 125 130 135 140 145 150 155 160 165 170 175
 180 185 190 195 200 205 210 215 220 225 230 235 240 245 250 255 260 265
 270 275 280 285 290 295 300 305 310 315 320 325 330 335 340 345 350 355] lat_range: [-90 -85 -80 -75 -70 -65 -60 -55 -50 -45 -40 -35 -30 -25 -20 -15 -10  -5
   0   5  10  15  20  25  30  35  40  45  50  55  60  65  70  75  80  85]
1894158     8.710762
1894159     6.773923
1894160     8.613117
1894161     4.430523
1894162     2.111511
             ...    
6242761    17.853312
6242762    20.574619
6242763    20.871948
6242764    20.241003
6242765    17.448559
Name: ve_anom, Length: 2017, dtype: float64


TypeError: cannot convert the series to <class 'float'>